| ![nsdf](https://www.sci.utah.edu/~pascucci/public/NSDF-smaller.PNG)  | [National Science Data Fabric](https://nationalsciencedatafabric.org/) [Jupyter notebook](https://jupyter.org/) <br> created by  [Valerio Pascucci](http://cedmav.com/) and  [Giorgio Scorzelli](https://www.sci.utah.edu/people/scrgiorgio.html)  |  
|---|:---:|


#  <center> This is a preview of the data:
![Visualization of Covid-19 cases](https://www.sci.utah.edu/~pascucci/public/CHESS-visus_recon_combined_1_2_3_fullres_zip.gif)

# Import OpenVisus and load dataset

In [1]:
import os,sys,logging,time

#sys.path.append("c:/projects/openvisus/build/RelWithDebInfo")
#sys.path.append("c:/projects/openvisuspy/src")

from IPython.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

from openvisuspy import LoadDataset, ExecuteBoxQuery, SetupLogger ,GetBackend
logger=SetupLogger(stream=False)
logger.info(f"GetBackend={GetBackend()}")

url='https://atlantis.sci.utah.edu/mod_visus?dataset=chess-recon_combined_1_2_3_fullres_zip&cached=1'
db=LoadDataset(url)
access=db.createAccess()
print(db.getDatasetBody().toString())

<dataset url="https://atlantis.sci.utah.edu:443/mod_visus?dataset=chess%2Drecon%5Fcombined%5F1%5F2%5F3%5Ffullres%5Fzip" cache_dir="" typename="IdxDataset">
	<access type="multiplex">
		<access type="IdxDiskAccess" chmod="rw" compression="zip" cache_dir="./visus-cache" />
		<access type="ModVisusAccess" chmod="r" />
	</access>
	<idxfile>
		<version value="6" />
		<bitmask value="V2012012012012012012012012012012" />
		<box value="0 912 0 816 0 2025" />
		<bitsperblock value="16" />
		<blocksperfile value="128" />
		<block_interleaving value="0" />
		<filename_template value="./visus/%04x.bin" />
		<missing_blocks value="False" />
		<arco value="0" />
		<time_template value="" />
		<axis value="" />
		<field name="data" description="" index="" default_compression="zip" default_layout="" default_value="0" filter="" dtype="float32" />
		<timestep when="0" />
	</idxfile>
</dataset>


# Show data

In [2]:
import numpy as np

import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

import panel as pn
pn.extension('vtk') # VTK is needed for  VTKVolumePlot 

def MyApp(endh=21, height=800):

    data=list(ExecuteBoxQuery(db,access=access,endh=endh,timestep=0,num_refinements=1))[0]['data']
    m,M=np.min(data),np.max(data)
    print(f"db.read returned shape={data.shape} dtype={data.dtype} range=[{m},{M}]")

     # generate a panel for numpy data
    volume = pn.panel(
        data, 
        sizing_mode='stretch_both', 
        orientation_widget =True,
        display_slices=True,
        spacing = (1, 1, 1),
        controller_expanded=False)

    # other widgets, with callbacks
    experiment  = pn.widgets.IntSlider(name='Experiment', start=0, end=1, step=1, value=0 )
    @pn.depends(experiment)
    def experiment_callback(value):
        nonlocal volume
        data=list(ExecuteBoxQuery(db,access=access, endh=endh,timestep=value,num_refinements=1))[0]['data']
        volume.object = data
        return " "    
    
    slider_i = pn.widgets.IntSlider(name='i-slice', start=0, end=data.shape[0], value = data.shape[0]//2 )
    @pn.depends(slider_i)
    def slider_i_callback(value):
        nonlocal volume
        volume.slice_i = value 
        return " "    
    
    slider_j = pn.widgets.IntSlider(name='j-slice', start=0, end=data.shape[1], value = data.shape[1]//2 )
    @pn.depends(slider_j)
    def slider_j_callback(value):
        nonlocal volume
        volume.slice_j = value 
        return " "    
    
    slider_k = pn.widgets.IntSlider(name='k-slice', start=0, end=data.shape[2], value = data.shape[2]//2 )
    @pn.depends(slider_k)
    def slider_k_callback(value):
        nonlocal volume
        volume.slice_k = value 
        return " "    
    
    show_volume = pn.widgets.Checkbox(name='Show Volume',value=True)
    @pn.depends(show_volume)
    def show_volume_callback(value):
        nonlocal volume
        volume.display_volume = value 
        return " "    
    
    show_slices = pn.widgets.Checkbox(name='Show Slices',value=True)
    @pn.depends(show_slices)
    def show_slices_calback(value):
        nonlocal volume
        volume.display_slices = value 
        return " "    

    main_layout=pn.Column(
        experiment,
        slider_i,
        slider_j,
        slider_k,
        pn.Row(
            show_volume,
            show_slices
        ),
        volume, 
        experiment_callback,
        slider_i_callback,
        slider_j_callback,
        slider_k_callback,
        show_volume_callback,
        show_slices_calback,
        height = height,
        css_classes=['panel-widget-box'],
        sizing_mode='stretch_width',
        width_policy='max')

    return main_layout

MyApp()

db.read returned shape=(126, 102, 114) dtype=float32 range=[-0.0013281364226713777,0.002098889322951436]


Column(css_classes=['panel-widget-box'], height=800, sizing_mode='stretch_width', width_policy='max')
    [0] IntSlider(name='Experiment')
    [1] IntSlider(end=126, name='i-slice', value=63)
    [2] IntSlider(end=102, name='j-slice', value=51)
    [3] IntSlider(end=114, name='k-slice', value=57)
    [4] Row
        [0] Checkbox(name='Show Volume', value=True)
        [1] Checkbox(name='Show Slices', value=True)
    [5] VTKVolume(ndarray, controller_expanded=False, display_slices=True, orientation_widget=True, sizing_mode='stretch_both', slice_i=63, slice_j=51, slice_k=57)
    [6] ParamFunction(function, _pane=Markdown, defer_load=False)
    [7] ParamFunction(function, _pane=Markdown, defer_load=False)
    [8] ParamFunction(function, _pane=Markdown, defer_load=False)
    [9] ParamFunction(function, _pane=Markdown, defer_load=False)
    [10] ParamFunction(function, _pane=Markdown, defer_load=False)
    [11] ParamFunction(function, _pane=Markdown, defer_load=False)

---------------------------
Copyright (c) 2021 **Valerio Pascucci & Giorgio Scorzelli** 

Permission is hereby granted, free of charge, to any person obtaining a copy of this software and associated documentation files (the "Software"), to deal in the Software without restriction, including without limitation the rights to use, copy, modify, merge, publish, distribute, sublicense, and/or sell copies of the Software, and to permit persons to whom the Software is furnished to do so, subject to the following conditions:

**The above copyright notice and this permission notice shall be included in all copies or substantial portions of the Software.** 

THE SOFTWARE IS PROVIDED "AS IS", WITHOUT WARRANTY OF ANY KIND, EXPRESS OR
IMPLIED, INCLUDING BUT NOT LIMITED TO THE WARRANTIES OF MERCHANTABILITY,
FITNESS FOR A PARTICULAR PURPOSE AND NONINFRINGEMENT. IN NO EVENT SHALL THE
AUTHORS OR COPYRIGHT HOLDERS BE LIABLE FOR ANY CLAIM, DAMAGES OR OTHER
LIABILITY, WHETHER IN AN ACTION OF CONTRACT, TORT OR OTHERWISE, ARISING FROM,
OUT OF OR IN CONNECTION WITH THE SOFTWARE OR THE USE OR OTHER DEALINGS IN THE
SOFTWARE.